# Part 1- Properties of vedio segementation

In [1]:
# ALGORITHM 1
import cv2
import numpy as np
cap = cv2.VideoCapture('test.mp4')

ret, prev_frame = cap.read()
prev_frame_gray = cv2.cvtColor(prev_frame, cv2.COLOR_BGR2GRAY)
prev_points = cv2.goodFeaturesToTrack(prev_frame_gray, maxCorners=100, qualityLevel=0.3, minDistance=7)
i=0
# Create the background subtractor object (MOG2 algorithm)
bg_subtractor = cv2.createBackgroundSubtractorMOG2()
# Initialize variables for statistical features
motion_magnitudes = []
while True:
    # Read the next frame
    ret, frame = cap.read()
    if not ret:
        break

    # Convert frames to grayscale
    frame_gray = cv2.cvtColor(frame, cv2.COLOR_BGR2GRAY)
    # Calculate Lucas-Kanade optical flow
    next_points, status, _ = cv2.calcOpticalFlowPyrLK(prev_frame_gray, frame_gray, prev_points, None)

    # Access flow information for a specific point
    point_index = 0
    x_prev, y_prev = prev_points[point_index].ravel()
    x_next, y_next = next_points[point_index].ravel()

    # Extract motion vector components
    dx = x_next - x_prev
    dy = y_next - y_prev

    # Calculate flow magnitude and angle
    magnitude = np.sqrt(dx**2 + dy**2)
    angle = np.arctan2(dy, dx)

    # Apply background subtraction
    foreground_mask = bg_subtractor.apply(frame)

    # Perform morphological operations (e.g., dilation, erosion) to refine object boundaries

    # Find contours of the foreground objects
    contours, _ = cv2.findContours(foreground_mask, cv2.RETR_EXTERNAL, cv2.CHAIN_APPROX_SIMPLE)

    # Compute segmentation confidence based on the area of each contour
    total_area = frame.shape[0] * frame.shape[1]
    confidence = []
    for contour in contours:
        contour_area = cv2.contourArea(contour)
        segment_confidence = contour_area / total_area
        confidence.append(segment_confidence)

    # Draw the object boundaries and segmentation confidence on the original frame
    frame_with_boundaries = frame.copy()
    for i, contour in enumerate(contours):
        cv2.drawContours(frame_with_boundaries, [contour], -1, (0, 255, 0), 2)

    # Calculate motion vectors
    motion_vectors = next_points - prev_points

    # Extract motion vector magnitudes
    motion_magnitudes.extend(np.linalg.norm(motion_vectors, axis=2).flatten())
    # Display the resulting frame
    cv2.imshow('Foreground Objects', foreground_mask) #b/w
    cv2.imshow('Object Boundaries', frame_with_boundaries)
    i+=1
    # Calculate statistical features
    mean_magnitude = np.mean(motion_magnitudes)
    std_dev_magnitude = np.std(motion_magnitudes)
    min_magnitude = np.min(motion_magnitudes)
    max_magnitude = np.max(motion_magnitudes)
    histogram, _ = np.histogram(motion_magnitudes, bins=10)
    if(i%50==0):
        print("Confidence: ",confidence)
        # Print flow information
        print("Motion vector: (", dx, ",", dy, ")")
        print("Magnitude:", magnitude)
        print("Angle:", angle)
        # Print statistical features
        print("Mean Magnitude:", mean_magnitude)
        print("Standard Deviation Magnitude:", std_dev_magnitude)
        print("Minimum Magnitude:", min_magnitude)
        print("Maximum Magnitude:", max_magnitude)
        print("Motion Magnitude Histogram:", histogram)

    # Exit loop when 'q' is pressed
    if cv2.waitKey(1) & 0xFF == ord('q'):
        break

# Release the video capture and close all windows
cap.release()
cv2.destroyAllWindows()


C:\Users\kausa\AppData\Local\Temp\ipykernel_10560\2449131040.py:33: RuntimeWarning: invalid value encountered in sqrt
  magnitude = np.sqrt(dx*2 + dy*2)


Confidence:  [0.0, 0.0, 0.0, 0.0, 0.0, 2.022653721682848e-05, 0.0, 5.056634304207119e-07, 0.0, 1.26415857605178e-06, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.52831715210356e-06, 0.0, 0.0, 4.121156957928803e-05, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0113268608414239e-06, 5.612864077669903e-05, 0.0, 2.5283171521035597e-07, 0.0, 1.8456715210355987e-05, 0.0, 0.0, 0.0, 0.0, 0.0, 5.056634304207119e-07, 0.0, 1.0113268608414239e-06, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 3.7924757281553396e-06, 0.0, 2.0226537216828478e-06, 1.9720873786407766e-05, 0.0, 0.0, 0.0, 5.056634304207119e-07, 0.0, 2.5283171521035597e-07, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 5.056634304207119e-07, 1.26415857605178e-06, 9.101941747572816e-06, 2.2249190938511326e-05, 0.0, 0.0, 1.4917071197411004e-05, 2.5283171521035597e-07, 0.0, 0.0, 0.0, 9.101941747572816e-06, 0.0, 0.0, 0.0, 1.7698220064724919e-06, 3.286812297734628e-05, 7.58495145631068e-07, 1.0113268608414239e-06, 0.0, 7

Confidence:  [0.0, 1.0113268608414239e-06, 1.7192556634304205e-05, 0.0, 0.0, 0.0, 4.8290857605177994e-05, 5.815129449838187e-06, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 7.0792880258899676e-06, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.5283171521035597e-07, 0.0, 0.0, 0.0, 0.0, 1.7698220064724919e-06, 1.3147249190938512e-05, 0.0, 0.0, 0.0, 1.0113268608414239e-06, 2.5283171521035597e-07, 2.5283171521035597e-07, 0.0, 0.0, 5.056634304207119e-07, 0.0, 0.0, 0.0, 0.0, 3.5396440129449838e-06, 1.0113268608414239e-06, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 5.157766990291262e-05, 0.0, 0.0, 2.5283171521035597e-07, 0.0, 0.0, 5.056634304207119e-07, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.5283171521035597e-07, 0.0, 0.0, 1.6686893203883495e-05, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.7698220064724919e-06, 2.5283171521035597e-07, 0.0, 2.5283171521035597e-07, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 4.0453074433656955e-06, 5.056634304207119e-07, 0.0, 2.5283171521035597e-07, 0.0, 2.78114886731391

Confidence:  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.7698220064724919e-06, 0.0, 2.0226537216828478e-06, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.7811488673139158e-06, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.7698220064724919e-06, 0.0, 0.0, 0.0, 3.7924757281553396e-06, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 7.58495145631068e-07, 0.0, 0.0, 2.5283171521035597e-07, 0.0, 3.5396440129449838e-06, 0.0, 5.815129449838187e-06, 0.0, 0.0, 2.0226537216828478e-06, 0.0, 0.0, 1.26415857605178e-06, 0.0, 0.0, 2.5283171521035597e-07, 0.0, 0.0, 0.0, 0.0, 0.0, 3.38794498381877e-05, 0.0, 1.2894417475728155e-05, 0.0, 8.84911003236246e-06, 0.0, 0.0, 0.0, 1.0113268608414239e-06, 5.056634304207119e-07, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.0226537216828478e-06, 0.0, 0.0, 0.0, 0.0, 0.0, 7.58495145631068e-07, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 5.309466019417476e-06, 7.58495145631068e-07, 5.056634304207119e-07, 0.0, 0.0, 0.0, 3.5396440129449838e-06, 0.0, 5.056634304207119e-07, 0.0, 2.78114

Confidence:  [0.0, 0.0, 0.0, 5.056634304207119e-07, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.5283171521035597e-07, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 5.05663430420712e-06, 1.7698220064724919e-06, 0.0, 0.0, 0.0, 0.0, 0.0, 2.5283171521035597e-07, 0.0, 2.5283171521035597e-07, 0.0, 0.0, 2.5283171521035597e-07, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.7698220064724919e-06, 5.056634304207119e-07, 0.0, 0.0, 0.0, 2.5283171521035597e-07, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 5.056634304207119e-07, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 7.58495145631068e-07, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 4.0453074433656955e-06, 5.056634304207119e-07, 3.5396440129449838e-06, 0.0, 0.0, 0.0, 2.52831715210356e-06, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.5283171521035597e-07, 0.0, 0.0, 2.5283171521035597e-07, 0.0, 0.0, 1.0113268608414239e-06, 1.26415857605178e-06, 0.0, 3.7924757281553396

...

Confidence:  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 5.056634304207119e-07, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.5283171521035597e-07, 0.0, 0.0, 0.0, 0.0, 7.58495145631068e-07, 0.0, 0.0, 2.5283171521035597e-07, 2.5283171521035597e-07, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 5.056634304207119e-07, 0.0, 2.5283171521035597e-07, 0.0, 1.26415857605178e-06, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.5283171521035597e-07, 0.0, 0.0, 7.584951456310679e-06, 0.0, 0.0, 0.0, 2.5283171521035597e-07, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.1490695792880258e-05, 1.26415857605178e-06, 0.0, 2.5283171521035597e-07, 0.0, 4.550970873786408e-06, 0.0, 3.033980582524272e-06, 1.1124595469255663e-05, 0.0, 0.0, 0.0, 0.0, 0.0, 2.5283171521035597e-07, 0.0, 0.0, 0.0, 0.0, 0.0, 2.5283171521035597e-07, 0.0, 2.5283171521035597e-07, 1.1124595469255663e-05, 2.5283171521035597e-07, 0.0, 4.0453074433656955e-06, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.5283171521035

Confidence:  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.5283171521035597e-07, 0.0, 0.0, 2.5283171521035597e-07, 1.7698220064724919e-06, 7.58495145631068e-07, 2.5283171521035597e-07, 0.0, 0.0, 2.0226537216828478e-06, 0.0, 0.0, 0.0, 0.0, 0.0, 1.26415857605178e-06, 0.0, 0.0, 0.0, 0.0, 3.033980582524272e-06, 7.58495145631068e-07, 0.0, 0.0, 4.550970873786408e-06, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.275485436893204e-06, 0.0, 0.0, 0.0, 0.0, 2.5283171521035597e-07, 0.0, 0.0, 0.0, 5.056634304207119e-07, 2.5283171521035597e-07, 0.0, 4.803802588996764e-06, 2.5283171521035597e-07, 0.0, 0.0, 4.803802588996764e-06, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.5283171521035597e-07, 0.0, 0.0, 0.0, 0.0, 5.056634304207119e-07, 0.0, 2.5283171521035597e-07, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.5283171521035597e-07, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 3.5396440129449838e-06, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.5283171521035597e-07, 4.298139158576051e-06, 0.0, 0.0, 0.0,

Confidence:  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 5.056634304207119e-07, 0.0, 2.5283171521035597e-07, 1.26415857605178e-06, 0.0, 0.0, 0.0, 0.0, 0.0, 7.58495145631068e-07, 0.0, 0.0, 0.0, 5.056634304207119e-07, 0.0, 2.5283171521035597e-07, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0618932038834951e-05, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 3.7924757281553396e-06, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 7.58495145631068e-07, 0.0, 0.0, 0.0, 2.0226537216828478e-06, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 4.298139158576051e-06, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.52831715210356e-06, 0.0, 0.0, 0.0, 0.0, 0.0, 5.056634304207119e-07, 0.0, 9.354773462783171e-06, 0.0, 0.0, 0.0, 0.0, 0.0, 2.5283171521035597e-07, 0.0, 0.0, 0.0, 2.5283171521035597e-07, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.5283171521035597e-07, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.5283171521035597e-07, 0.0, 0.0, 0.0, 0.0, 0.0, 2.528317152103559

Confidence:  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.516990291262136e-06, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.516990291262136e-06, 2.5283171521035597e-07, 0.0, 5.056634304207119e-07, 0.0, 0.0, 0.0, 0.0, 7.58495145631068e-07, 0.0, 0.0, 0.0, 7.58495145631068e-07, 5.05663430420712e-06, 1.7698220064724919e-06, 0.0, 4.0453074433656955e-06, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.5283171521035597e-07, 5.056634304207119e-07, 0.0, 0.0, 2.5283171521035597e-07, 2.5283171521035597e-07, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.5283171521035597e-07, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 5.056634304207119e-07, 0.0, 0.0, 0.0, 2.5283171521035597e-07, 0.0, 4.550970873786408e-06, 0.0, 0.0, 2.5283171521035597e-07, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 6.826456310679612e-06, 0.0, 0.0, 0.0, 0.0, 0.0, 5.5622977346278315e-06, 0.0, 0.0, 5.056634304207119e-07, 0.0, 0.0, 0.0, 2.5283

Confidence:  [3.944174757281553e-05, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.5169902912621359e-05, 0.0, 0.0, 4.550970873786408e-06, 0.0, 0.0, 0.0, 0.0, 2.5283171521035597e-07, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.5283171521035597e-07, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 4.298139158576051e-06, 0.0, 0.0, 2.5283171521035597e-07, 5.309466019417476e-06, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 6.067961165048544e-06, 2.275485436893204e-06, 0.0, 2.5283171521035597e-07, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0871763754045308e-05, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.7698220064724919e-06, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.5675566343042072e-05, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 5.056634304207119e-07, 2.5283171521035597e-07, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.5283171521035597e-07, 0.0, 0.0, 0.0, 0.0, 1.2388754045307443e-

In [4]:
#ALGORITHM 2
import cv2
import numpy as np

cap = cv2.VideoCapture('test.mp4')

# Read the first frame
ret, prev_frame = cap.read()
prev_frame = cv2.cvtColor(prev_frame, cv2.COLOR_BGR2GRAY)
i=0
while True:
    # Read the next frame
    ret, frame = cap.read()
    if not ret:
        break

    # Convert frames to grayscale
    frame_gray = cv2.cvtColor(frame, cv2.COLOR_BGR2GRAY)

    # Calculate dense optical flow
    flow = cv2.calcOpticalFlowFarneback(prev_frame, frame_gray, None, 0.5, 3, 15, 3, 5, 1.2, 0)

    # Compute statistical features of flow vectors
    flow_magnitude = np.sqrt(flow[..., 0] ** 2 + flow[..., 1] ** 2)
    mean_magnitude = np.mean(flow_magnitude)
    std_dev_magnitude = np.std(flow_magnitude)
    # Add more statistical features as needed

    # Calculate motion information
    motion_threshold = 10
    motion_pixels = np.sum(flow_magnitude > motion_threshold)

    # Calculate segmentation confidence or probability (example: using flow magnitude)
    segmentation_confidence = flow_magnitude / np.max(flow_magnitude)

    # Visualize flow vectors
    flow_visualization = cv2.cvtColor(frame_gray, cv2.COLOR_GRAY2BGR)
    flow_x = flow[..., 0]
    flow_y = flow[..., 1]
    flow_visualization[..., 0] += cv2.convertScaleAbs(flow_x)
    flow_visualization[..., 1] += cv2.convertScaleAbs(flow_y)
    cv2.imshow('Optical Flow', flow_visualization)

    # Extract object boundaries (e.g., using edge detection or contour detection)
    edges = cv2.Canny(flow_visualization, threshold1=50, threshold2=200)
    cv2.imshow('Object Boundaries', edges)

    # Print the properties
    i=i+1
    if i%20==0:
        print('Mean Magnitude:', mean_magnitude)
        print('Standard Deviation of Magnitude:', std_dev_magnitude)
        print('Motion Pixels:', motion_pixels)
        print('Segmentation Confidence:', segmentation_confidence)

    # Exit loop when 'q' is pressed
    if cv2.waitKey(1) & 0xFF == ord('q'):
        break

    # Update the previous frame
    prev_frame = frame_gray.copy()

# Release the video capture and close all windows

cap.release()
cv2.destroyAllWindows()


Mean Magnitude: 0.00083983934
Standard Deviation of Magnitude: 0.031713996
Motion Pixels: 0
Segmentation Confidence: [[0.0000000e+00 0.0000000e+00 0.0000000e+00 ... 4.7901612e-02
  5.1497690e-02 5.4432295e-02]
 [0.0000000e+00 0.0000000e+00 0.0000000e+00 ... 4.9430978e-02
  5.3058032e-02 5.6014199e-02]
 [0.0000000e+00 0.0000000e+00 0.0000000e+00 ... 5.1176459e-02
  5.4840211e-02 5.7825956e-02]
 ...
 [9.7058660e-07 1.6545040e-06 2.4937788e-06 ... 3.2734274e-06
  3.0708791e-06 2.7283456e-06]
 [7.5968052e-07 1.4374034e-06 2.3102587e-06 ... 3.0357030e-06
  2.8650711e-06 2.5958905e-06]
 [5.4467398e-07 1.0046703e-06 1.6611066e-06 ... 2.6146756e-06
  2.4869100e-06 2.2967358e-06]]
Mean Magnitude: 0.12308283
Standard Deviation of Magnitude: 0.18010871
Motion Pixels: 0
Segmentation Confidence: [[3.33024422e-03 3.22210020e-03 3.20904399e-03 ... 7.03353144e-05
  7.71297055e-05 7.97281100e-05]
 [3.57547984e-03 3.48931318e-03 3.45933414e-03 ... 7.28558371e-05
  7.92201754e-05 8.20341520e-05]
 [3.9242

Mean Magnitude: 0.1843711
Standard Deviation of Magnitude: 0.23142608
Motion Pixels: 0
Segmentation Confidence: [[0.01539651 0.0108073  0.02509907 ... 0.01757305 0.01970492 0.02206944]
 [0.03566537 0.0130016  0.01075184 ... 0.01404379 0.01547792 0.01702765]
 [0.05123051 0.02756415 0.00186515 ... 0.01101893 0.0120285  0.01318611]
 ...
 [0.10579247 0.08917235 0.07233749 ... 0.01490805 0.01510552 0.01394268]
 [0.09509195 0.07894754 0.05590818 ... 0.01195798 0.01191702 0.01071466]
 [0.08303929 0.06757448 0.04164875 ... 0.00758195 0.00735455 0.00638768]]
Mean Magnitude: 8.02673
Standard Deviation of Magnitude: 10.858308
Motion Pixels: 568609
Segmentation Confidence: [[1.11101933e-01 1.03059009e-01 1.00982159e-01 ... 9.63011989e-04
  1.57126389e-03 2.21115840e-03]
 [1.09172270e-01 1.00575596e-01 9.84784961e-02 ... 1.54257391e-03
  2.05607642e-03 2.61443015e-03]
 [1.07889071e-01 9.88451317e-02 9.68296155e-02 ... 2.01282511e-03
  2.39328574e-03 2.90576089e-03]
 ...
 [1.37535346e-04 1.58009690e

Mean Magnitude: 2.8987138
Standard Deviation of Magnitude: 5.826666
Motion Pixels: 146623
Segmentation Confidence: [[4.20986600e-02 4.33224365e-02 4.38442416e-02 ... 4.51128726e-05
  2.91670494e-05 2.22639173e-05]
 [4.57338430e-02 4.67782207e-02 4.74625267e-02 ... 3.40956030e-05
  2.44331586e-05 2.22896579e-05]
 [4.91237491e-02 4.99362387e-02 5.07169589e-02 ... 2.80326240e-05
  2.37128424e-05 2.42729129e-05]
 ...
 [1.24966055e-02 1.57617629e-02 1.55410562e-02 ... 4.71891537e-02
  4.81819808e-02 4.81479764e-02]
 [6.77753845e-03 9.55134071e-03 9.73149110e-03 ... 3.02828550e-02
  3.20614204e-02 3.38538997e-02]
 [3.82356439e-03 6.12828881e-03 6.49595493e-03 ... 2.00792030e-02
  2.12882776e-02 2.28945091e-02]]
Mean Magnitude: 0.11863196
Standard Deviation of Magnitude: 0.1867929
Motion Pixels: 0
Segmentation Confidence: [[0.02208692 0.02328633 0.02333887 ... 0.006016   0.00639319 0.00650271]
 [0.01839297 0.01951728 0.01953894 ... 0.00640379 0.00671912 0.00667395]
 [0.01560657 0.01652753 0.0

# PART 2- Keyframe Extraction 

In [1]:
#1. Keyframe Duration
#2. Keyframe Metadata
import cv2
def extract_keyframes(video_path, keyframe_interval):
    keyframes = []
    durations = []
    metadata = []
    
    cap = cv2.VideoCapture('test.mp4')
    frame_count = 0
    current_frame = 0
    
    while cap.isOpened():
        ret, frame = cap.read()
        
        if not ret:
            break
        
        frame_count += 1
        
        if frame_count % keyframe_interval == 0:
            keyframes.append(frame)

            durations.append(cap.get(cv2.CAP_PROP_POS_MSEC) / 1000.0)
            cv2.imshow('Keyframe', frame)
            if cv2.waitKey(1) & 0xFF == ord('q'):
                break
            metadata.append({
                'frame_number': frame_count,
                'timestamp': cap.get(cv2.CAP_PROP_POS_MSEC) / 1000.0
            })
            
    cap.release()
    return durations, metadata

# Example usage
video_path = 'test.mp4'
keyframe_interval = 30  # Extract keyframes every 30 frames

durations, metadata = extract_keyframes(video_path, keyframe_interval)

# Print the results in the table format
print("Properties\tOutput")
print("Keyframe duration:\t", durations)
print("Keyframe metadata:\t", metadata)

Properties	Output
Keyframe duration	 [0.9666666666666667, 1.9666666666666668, 2.966666666666667, 3.966666666666667, 4.966666666666667, 5.966666666666667, 6.966666666666667, 7.966666666666667, 8.966666666666667, 9.966666666666667, 10.966666666666667, 11.966666666666667, 12.966666666666667, 13.966666666666667, 14.966666666666667, 15.966666666666667, 16.96666666666667, 17.96666666666667, 18.96666666666667, 19.96666666666667, 20.96666666666667, 21.96666666666667, 22.96666666666667, 23.96666666666667]
Keyframe metadata	 [{'frame_number': 30, 'timestamp': 0.9666666666666667}, {'frame_number': 60, 'timestamp': 1.9666666666666668}, {'frame_number': 90, 'timestamp': 2.966666666666667}, {'frame_number': 120, 'timestamp': 3.966666666666667}, {'frame_number': 150, 'timestamp': 4.966666666666667}, {'frame_number': 180, 'timestamp': 5.966666666666667}, {'frame_number': 210, 'timestamp': 6.966666666666667}, {'frame_number': 240, 'timestamp': 7.966666666666667}, {'frame_number': 270, 'timestamp': 8.96

In [4]:
#3. Image Quality metrics 
import cv2
import numpy as np
from skimage.metrics import structural_similarity as ssim

# Load video
video = cv2.VideoCapture("test.mp4") 

# Initialize variables
psnr_values = []
ssim_values = []
frame_count = 0

while True:
    # Read frame from the video
    ret, frame = video.read()

    if not ret:
        break

    # Convert frame to grayscale
    gray_frame = cv2.cvtColor(frame, cv2.COLOR_BGR2GRAY)

    if frame_count > 0:
        # Calculate PSNR
        psnr = cv2.PSNR(prev_frame, gray_frame)
        psnr_values.append(psnr)

        # Calculate SSIM
        ssim_score = ssim(prev_frame, gray_frame, data_range=gray_frame.max() - gray_frame.min())
        ssim_values.append(ssim_score)

    # Set current frame as previous frame for the next iteration
    prev_frame = gray_frame.copy()

    frame_count += 1

# Calculate average PSNR and SSIM
average_psnr = np.mean(psnr_values)
average_ssim = np.mean(ssim_values)

# Print the results
print("Average PSNR:", average_psnr)
print("Average SSIM:", average_ssim)

# Release video capture
video.release()


Average PSNR: 30.927642056548773
Average SSIM: 0.8242561147752977


In [5]:
#4. Scene Transition
import cv2

def detect_scene_transitions(video_path):
    cap = cv2.VideoCapture(video_path)
    if not cap.isOpened():
        print("Error opening video file")
        return

    frame_width = int(cap.get(cv2.CAP_PROP_FRAME_WIDTH))
    frame_height = int(cap.get(cv2.CAP_PROP_FRAME_HEIGHT))
    frame_count = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))
    fps = cap.get(cv2.CAP_PROP_FPS)

    prev_frame = None
    scene_transitions = []

    for frame_idx in range(frame_count):
        ret, frame = cap.read()
        if not ret:
            break

        # Convert frame to grayscale for analysis
        gray_frame = cv2.cvtColor(frame, cv2.COLOR_BGR2GRAY)
        gray_frame = cv2.GaussianBlur(gray_frame, (5, 5), 0)  # Apply blur to reduce noise

        if prev_frame is not None:
            # Compute absolute difference between current and previous frame
            frame_diff = cv2.absdiff(gray_frame, prev_frame)

            # Threshold the frame difference
            _, threshold = cv2.threshold(frame_diff, 30, 255, cv2.THRESH_BINARY)

            # Count the number of non-zero pixels in the thresholded frame
            pixel_count = cv2.countNonZero(threshold)

            # Adjust the threshold based on frame size and pixel count
            threshold_limit = frame_width * frame_height * 0.01  # Adjust this value as needed
            if pixel_count > threshold_limit:
                scene_transitions.append(frame_idx)

        prev_frame = gray_frame

    cap.release()

    return scene_transitions

# Example usage
video_path = "test.mp4"
transitions = detect_scene_transitions(video_path)
print("Scene transitions detected at frames:", transitions)

Scene transitions detected at frames: [25, 27, 28, 30, 31, 33, 34, 37, 38, 39, 42, 43, 46, 47, 49, 50, 51, 53, 54, 56, 57, 59, 60, 62, 63, 65, 66, 68, 69, 71, 74, 75, 76, 78, 79, 81, 82, 84, 85, 86, 88, 89, 91, 92, 94, 95, 97, 98, 100, 102, 104, 105, 107, 108, 109, 110, 111, 112, 113, 114, 116, 117, 118, 119, 120, 121, 122, 125, 126, 127, 128, 130, 131, 133, 134, 136, 137, 139, 140, 141, 142, 144, 145, 146, 148, 149, 151, 152, 154, 155, 156, 158, 159, 161, 162, 163, 165, 166, 168, 170, 174, 176, 177, 178, 180, 181, 183, 184, 185, 187, 188, 189, 191, 192, 194, 195, 196, 198, 199, 201, 202, 203, 204, 206, 207, 209, 210, 211, 213, 214, 215, 217, 218, 219, 220, 221, 223, 224, 226, 227, 228, 230, 231, 232, 233, 235, 236, 238, 239, 241, 242, 244, 245, 246, 248, 249, 251, 252, 254, 257, 258, 259, 260, 261, 262, 264, 265, 267, 268, 269, 271, 272, 274, 275, 277, 278, 279, 281, 282, 283, 285, 286, 287, 288, 289, 291, 292, 294, 295, 297, 298, 299, 301, 302, 304, 305, 306, 308, 311, 312, 313, 314,

In [6]:
import cv2

def detect_scene_transitions(video_path):
    cap = cv2.VideoCapture(video_path)

    if not cap.isOpened():
        print("Error opening video file")
        return

    # Read the first frame
    ret, prev_frame = cap.read()
    if not ret:
        print("Error reading video frame")
        return

    frame_count = 0
    transition_frames = []

    while True:
        ret, curr_frame = cap.read()
        if not ret:
            break

        # Compute the absolute difference between the current frame and the previous frame
        diff = cv2.absdiff(curr_frame, prev_frame)
        grayscale_diff = cv2.cvtColor(diff, cv2.COLOR_BGR2GRAY)

        # Apply a threshold to the difference image
        _, threshold_diff = cv2.threshold(grayscale_diff, 30, 255, cv2.THRESH_BINARY)

        # Calculate the percentage of white pixels in the thresholded image
        white_pixel_percentage = cv2.countNonZero(threshold_diff) / (threshold_diff.shape[0] * threshold_diff.shape[1])

        # Adjust the threshold and white pixel percentage thresholds to your specific needs
        if white_pixel_percentage > 0.02:
            transition_frames.append(curr_frame)
            print("Scene transition detected at frame:", frame_count)

        # Display the frames (optional)
        cv2.imshow("Current Frame", curr_frame)
        cv2.imshow("Difference", threshold_diff)

        # Press 'q' to exit
        if cv2.waitKey(1) & 0xFF == ord('q'):
            break

        prev_frame = curr_frame
        frame_count += 1

    cap.release()
    cv2.destroyAllWindows()

    return transition_frames

# Specify the path to your video file
video_path = "test.mp4"

# Call the function to detect scene transitions and get the transition frames
transition_frames = detect_scene_transitions(video_path)

# Save the transition frames as individual images
for i, frame in enumerate(transition_frames):
    cv2.imwrite(f"transition_frame_{i}.jpg", frame)


Scene transition detected at frame: 24
Scene transition detected at frame: 26
Scene transition detected at frame: 27
Scene transition detected at frame: 29
Scene transition detected at frame: 30
Scene transition detected at frame: 32
Scene transition detected at frame: 33
Scene transition detected at frame: 36
Scene transition detected at frame: 37
Scene transition detected at frame: 38
Scene transition detected at frame: 41
Scene transition detected at frame: 42
Scene transition detected at frame: 45
Scene transition detected at frame: 46
Scene transition detected at frame: 48
Scene transition detected at frame: 49
Scene transition detected at frame: 50
Scene transition detected at frame: 52
Scene transition detected at frame: 53
Scene transition detected at frame: 55
Scene transition detected at frame: 56
Scene transition detected at frame: 58
Scene transition detected at frame: 59
Scene transition detected at frame: 61
Scene transition detected at frame: 62
Scene transition detected

Scene transition detected at frame: 338
Scene transition detected at frame: 339
Scene transition detected at frame: 340
Scene transition detected at frame: 342
Scene transition detected at frame: 343
Scene transition detected at frame: 345
Scene transition detected at frame: 346
Scene transition detected at frame: 347
Scene transition detected at frame: 349
Scene transition detected at frame: 350
Scene transition detected at frame: 352
Scene transition detected at frame: 353
Scene transition detected at frame: 355
Scene transition detected at frame: 358
Scene transition detected at frame: 359
Scene transition detected at frame: 361
Scene transition detected at frame: 362
Scene transition detected at frame: 363
Scene transition detected at frame: 365
Scene transition detected at frame: 366
Scene transition detected at frame: 368
Scene transition detected at frame: 369
Scene transition detected at frame: 370
Scene transition detected at frame: 371
Scene transition detected at frame: 373


Scene transition detected at frame: 629
Scene transition detected at frame: 631
Scene transition detected at frame: 632
Scene transition detected at frame: 633
Scene transition detected at frame: 635
Scene transition detected at frame: 637
Scene transition detected at frame: 638
Scene transition detected at frame: 639
Scene transition detected at frame: 641
Scene transition detected at frame: 642
Scene transition detected at frame: 643
Scene transition detected at frame: 645
Scene transition detected at frame: 646
Scene transition detected at frame: 648
Scene transition detected at frame: 649
Scene transition detected at frame: 651
Scene transition detected at frame: 655
Scene transition detected at frame: 656
Scene transition detected at frame: 658
Scene transition detected at frame: 664
Scene transition detected at frame: 666
Scene transition detected at frame: 670
Scene transition detected at frame: 672
Scene transition detected at frame: 673
Scene transition detected at frame: 675


# PART 3- Object Tracking

In [2]:

#TRACKING WITH SIMPLE CENTROID TECHNIQUE

import numpy as np
import cv2
def find_center(hsv):
    h,s,v = cv2.split(hsv)
    ret,thresh = cv2.threshold(s,100,155,0)
    M = cv2.moments(thresh)
    cx = int(M['m10']/M['m00']) # Sum of mi*xi/sum of mi
    cy=int(M['m01']/M['m00'])   # Sum of mi*yi/sum of mi
    center=[cx,cy]
    return center   
# Create opencv video capture object
VideoCap = cv2.VideoCapture('test.mp4')
while(True):
       # Read frame
       ret, frame = VideoCap.read()
       # Detect object, by reading frame by frame
       hsv = cv2.cvtColor(frame,cv2.COLOR_BGR2HSV)
       center = find_center(hsv)
       z=[center[0],center[1]]
       cv2.circle(frame,center, 10, (0,255, 255), 2)  
       cv2.imshow('image',frame) 
       k = cv2.waitKey(30) & 0xff
       if k == 27:
           break
            
VideoCap.release()
cv2.destroyAllWindows()  

error: OpenCV(4.6.0) D:\a\opencv-python\opencv-python\opencv\modules\imgproc\src\color.cpp:182: error: (-215:Assertion failed) !_src.empty() in function 'cv::cvtColor'


Inference--> 
* Can detect only one pothole at a time in agiven vedio frame
* Fails for multiple potholes.
* Not very accurate

In [5]:
#Mean shift HSV -->
import numpy as np
import cv2

cap = cv2.VideoCapture('test.mp4')

# take first frame of the video
ret,frame = cap.read()

# setup initial location of window
# r,h,c,w - region of image
#           simply hardcoded the values
r,h,c,w = 200,20,300,20  
track_window = (c,r,w,h)

# set up the ROI for tracking
roi = frame[r:r+h, c:c+w]
hsv_roi =  cv2.cvtColor(frame, cv2.COLOR_BGR2HSV)
mask = cv2.inRange(hsv_roi, np.array((0., 60.,32.)), np.array((180.,255.,255.)))
roi_hist = cv2.calcHist([hsv_roi],[0],mask,[180],[0,180])
cv2.normalize(roi_hist,roi_hist,0,255,cv2.NORM_MINMAX)

# Setup the termination criteria, either 10 iteration or move by at least 1 pt
term_crit = ( cv2.TERM_CRITERIA_EPS | cv2.TERM_CRITERIA_COUNT, 10, 1 )

while(1):
    ret ,frame = cap.read()

    if ret == True:
        hsv = cv2.cvtColor(frame, cv2.COLOR_BGR2HSV)
        dst = cv2.calcBackProject([hsv],[0],roi_hist,[0,180],1)

        # apply meanshift to get the new location
        ret, track_window = cv2.meanShift(dst, track_window, term_crit)

        # Draw it on image
        x,y,w,h = track_window
        img2 = cv2.rectangle(frame, (x,y), (x+w,y+h), 255,2)
        cv2.imshow('img2',img2)

        k = cv2.waitKey(60) & 0xff
        if k == 27:
            break
        else:
            cv2.imwrite(chr(k)+".jpg",img2)

    else:
        break

cv2.destroyAllWindows()
cap.release()

Inference-->
* Does not give an accurate detectioon of the potholes 

In [2]:
#Camshift Algorithm
import numpy as np
import cv2

cap = cv2.VideoCapture('test.mp4')
ret, frame = cap.read()
x, y, w, h = cv2.selectROI("Select ROI", frame, False)
track_window = (x, y, w, h)
roi = frame[y:y + h, x:x + w]
hsv_roi = cv2.cvtColor(roi, cv2.COLOR_BGR2HSV)
mask = cv2.inRange(hsv_roi, np.array((0., 60., 32.)), np.array((180., 255., 255.)))
roi_hist = cv2.calcHist([hsv_roi], [0], mask, [180], [0, 180])
cv2.normalize(roi_hist, roi_hist, 0, 255, cv2.NORM_MINMAX)
term_crit = (cv2.TERM_CRITERIA_EPS | cv2.TERM_CRITERIA_COUNT, 10, 1)

while True:
    ret, frame = cap.read()
    
    if not ret:
        break
    
    hsv = cv2.cvtColor(frame, cv2.COLOR_BGR2HSV)
    dst = cv2.calcBackProject([hsv], [0], roi_hist, [0, 180], 1)
    ret, track_window = cv2.CamShift(dst, track_window, term_crit)
    pts = cv2.boxPoints(ret)
    pts = np.int0(pts)
    img2 = cv2.polylines(frame, [pts], True, (0, 255, 0), 2)
    
    cv2.imshow('img2', img2)
    if cv2.waitKey(1) & 0xFF == ord('q'):
        break

cap.release()
cv2.destroyAllWindows()

In [1]:
#Kalman filter
import cv2
import numpy as np


class KalmanFilter:
    def __init__(self):
        self.kalman = cv2.KalmanFilter(4, 2)
        self.kalman.measurementMatrix = np.array([[1, 0, 0, 0], [0, 1, 0, 0]], np.float32)
        self.kalman.transitionMatrix = np.array([[1, 0, 1, 0], [0, 1, 0, 1], [0, 0, 1, 0], [0, 0, 0, 1]], np.float32)

    def update(self, measurement):
        self.kalman.correct(measurement)

    def predict(self):
        return self.kalman.predict()


def detect_potholes(video_path):
    cap = cv2.VideoCapture('test.mp4')

    # Get the first frame for initialization
    ret, frame = cap.read()
    if not ret:
        raise ValueError("Unable to read video file")

    # Initialize the Kalman filters
    kalman_filters = []

    # Initialize the variables for drawing the output
    colors = np.random.randint(0, 255, (100, 3)).tolist()  # Convert to list

    # Define the parameters for object detection
    pothole_area_threshold = 500

    while True:
        ret, frame = cap.read()
        if not ret:
            break

        # Convert the frame to grayscale for object detection
        gray = cv2.cvtColor(frame, cv2.COLOR_BGR2GRAY)

        # Perform object detection using simple thresholding
        _, thresholded = cv2.threshold(gray, 150, 255, cv2.THRESH_BINARY)

        # Find contours in the thresholded image
        contours, _ = cv2.findContours(thresholded, cv2.RETR_EXTERNAL, cv2.CHAIN_APPROX_SIMPLE)

        for contour in contours:
            area = cv2.contourArea(contour)

            # Ignore small contours (noise)
            if area < pothole_area_threshold:
                continue

            # Compute the bounding box for the contour
            x, y, w, h = cv2.boundingRect(contour)

            # Initialize a new Kalman filter for the object
            kalman_filter = KalmanFilter()
            kalman_filter.update(np.array([[x + w / 2], [y + h / 2]], np.float32))
            kalman_filters.append(kalman_filter)

            # Draw the bounding box and label on the frame
            color = colors[len(kalman_filters) % len(colors)]
            cv2.rectangle(frame, (x, y), (x + w, y + h), color, 2)
            cv2.putText(frame, 'Pothole', (x, y - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.9, color, 2)

        # Update and predict the Kalman filters
        for kalman_filter in kalman_filters:
            prediction = kalman_filter.predict()
            x, y = prediction[0], prediction[1]

            # Draw the predicted position as a circle
            cv2.circle(frame, (int(x), int(y)), 5, (0, 255, 0), -1)

        # Display the output frame
        cv2.imshow('Pothole Detection', frame)

        # Exit if the 'q' key is pressed
        if cv2.waitKey(1) & 0xFF == ord('q'):
            break

    # Release the video capture and close all windows
    cap.release()
    cv2.destroyAllWindows()


# Run the pothole detection on a video
detect_potholes('test.mp4')


Inference-->
* Gives a good detection of the potholes
* Able to detect multiple poholes in the single rame of vedio